# Welcome!

In [1]:
# we start by importing modules
import warnings
warnings.filterwarnings('ignore')
import numpy as np
import pandas as pd
from vf_portalytics.model import PredictionModel
from vf_portalytics.dataset import DataSet
from vf_portalytics.tool import create_train_test_sets, score_model, describe_columns
from sklearn import linear_model, ensemble, svm

from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bkcharts import Histogram, Bar, Line, Scatter
from bkcharts.attributes import cat
output_notebook()

Loading BokehJS ...

In [2]:
# now we load data and create the basics
dataset = DataSet('x', path='/home/carst/')
df = dataset.data_df

In [3]:
# describe available columns
describe_columns(df)


Standard Columns: 
account_banner, account_id, base_price, baseline_units_ext, baseline_units_int, baseline_units, baseline_vol, discount_amount, discount_amt, discount_perc, fwb_post, fwb_pre, internal, lift, mechanism, multi_buy_x, multi_buy_y, promoted_base_price, promoted_price, promotion_id, promotion_name, promotion_status, second_placement_perc, second_placement_yn, total_baseline_units, total_baseline_vol, total_nr_products, total_units, total_vol, week_agg_2, week_agg_4, week_nr, week, weighted_distribution_normal, weighted_distribution_promoted

Promotion Fields: 
field_10, field_2, field_21, field_27, field_4, field_9

Tags: 
tag_feestdagen_carnaval_week_ervoor, tag_feestdagen_carnaval, tag_feestdagen_goede_vrijdag, tag_feestdagen_hemelvaartsdag, tag_feestdagen_kerst, tag_feestdagen_koningsdag, tag_feestdagen_moederdag_week_ervoor, tag_feestdagen_moederdag, tag_feestdagen_pasen_week_ervoor_, tag_feestdagen_pasen, tag_feestdagen_periode_tussen_kerst_en_oudamp_amp_nieuw, tag_

# Filter Dataframe

In [4]:
# filtering the contents
status_mask = df['promotion_status'] >= 112
df = df[status_mask]
print("\nAfter status filter: We have %d df with %d features." % (df.shape[0], df.shape[1]))

date_mask = df['field_21'] > 201600
df = df[date_mask]
print("\nAfter week filter: %d rows with %d features." % (df.shape[0], df.shape[1]))

small_df_mask = df['baseline_units'] > 0.0
df = df[small_df_mask]
print("\nAfter >0 baseline filter: %d rows with %d features." % (df.shape[0], df.shape[1]))

huge_df_mask = df['baseline_units'] < 10.0**5
df = df[huge_df_mask]
print("\nAfter <10k baseline filter: %d rows with %d features." % (df.shape[0], df.shape[1]))

small_lift_mask = (df['lift'] > 1.2) & (df['lift'] < 40)
df = df[small_lift_mask]
print("\nAfter lift filter: %d rows with %d features." % (df.shape[0], df.shape[1]))

min_discount_mask = (df['discount_perc'] >= 5.0) & (df['discount_perc'] < 75.0)
df = df[min_discount_mask]
print("\nAfter discount filter: %d rows with %d features." % (df.shape[0], df.shape[1]))

mechanism_msk = df['mechanism'].notnull()
df = df[mechanism_msk]
print("\nAfter mechanism filter: %d rows with %d features." % (df.shape[0], df.shape[1]))


After status filter: We have 119455 df with 229 features.

After week filter: 119455 rows with 229 features.

After >0 baseline filter: 95047 rows with 229 features.

After <10k baseline filter: 94997 rows with 229 features.

After lift filter: 78330 rows with 229 features.

After discount filter: 69700 rows with 229 features.

After mechanism filter: 69700 rows with 229 features.


# Investigate data

In [5]:
# distribution histograms 
check_list = ['discount_perc', 'account_banner', 'week_nr', 'baseline_units', 'mechanism']

# nb: we filter out the bottom and top 0.5%)
low_limit_def = 0.0
high_limit_def = 100.0
# nb: normal histograms are for numeric columns only, others are top 20 bar charts 
top_def = 20
df['count'] = 1  # nb: the count is the promotion - product combinations

# now plot
for col in check_list:
    if df[col].dtype in [np.int64, np.float64]:
        low_limit = np.percentile(df[col], low_limit_def)
        high_limit = np.percentile(df[col], high_limit_def)
        print('Showing ' + col + ' between ' + str(low_limit) + ' and ' + str(high_limit))
        mask = (df[col] >= low_limit) & (df[col] <= high_limit)
        p = Histogram(df[mask], values=col, bins=12)
        p.axis[1].axis_label = 'Count'
        show(p)
    else:
        print('Showing ' + col + ' top ' + str(top_def))
        group = df.groupby([col], as_index=False)['count'].sum()
        group[col] = group[col].str.encode('utf-8')
        group = group.nlargest(top_def, 'count')
        label = cat(columns=col, sort=False)
        p = Bar(group, label=label, values='count', legend=None)
        p.axis[1].axis_label = 'Count'
        show(p)  

Showing discount_perc between 5.0 and 74.95


Showing account_banner top 20


Showing week_nr between 1.0 and 52.0


Showing baseline_units between 0.714285714286 and 91370.0


Showing mechanism top 20


In [6]:
# charts that check against lift
check_list = ['discount_perc', 'account_banner', 'mechanism']

# now plot
for col in check_list:
    if df[col].dtype in [np.int64, np.float64]:
        print('Drawing Average Lift + Nr Observations for ' + col)
        df['tmp_col'] = df[col].round() 
        group = df.groupby(['tmp_col'], as_index=False)['baseline_units', 'total_units', 'count'].sum()
        del df['tmp_col']
        group['lift'] = group['total_units'] / group['baseline_units']
        group = group.rename(columns={'tmp_col': col})
        p = Line(group, x=col, y='lift')
        show(p)
        p = Line(group, x=col, y='count', color='green')
        show(p) 
    else:
        print('Showing ' + col + ' Average Lift for ' + str(top_def) + ' most used')
        group = df.groupby([col], as_index=False)['baseline_units', 'total_units', 'count'].sum()
        group[col] = group[col].str.encode('utf-8')
        group = group.nlargest(top_def, 'count')
        group['lift'] = group['total_units'] / group['baseline_units']
        label = cat(columns=col, sort=False)
        p = Bar(group, label=label, values='lift', legend=None)
        p.axis[1].axis_label = 'Avg Lift'
        show(p) 

Drawing Average Lift + Nr Observations for discount_perc


Showing account_banner Average Lift for 20 most used


Showing mechanism Average Lift for 20 most used


In [7]:
# plot scatter diagrams for correlation visualization
check_list = [('discount_perc', 'lift'), ('baseline_units', 'total_units')]

# now plot
for col_x, col_y in check_list:
    if df[col_x].dtype in [np.int64, np.float64] and df[col_y].dtype in [np.int64, np.float64]:
        print('Drawing Scatter Correlation for ' + col_x + ' and ' + col_y)
        p = Scatter(df, x=col_x, y=col_y)
        show(p)
    else:
        print('Both columns need to be numerical')

Drawing Scatter Correlation for discount_perc and lift


Drawing Scatter Correlation for baseline_units and total_units


# Create a model and select the features

In [8]:
# creating a prediction model
prediction_model = PredictionModel('carst_example', path='/home/carst/')

# set the features (C = categoric value for dimensional features)
prediction_model.features = {
    'baseline_units': [],
    'total_baseline_units': [],  # total to check the complete size of the promotion
    'total_nr_products': [],  # total to check the complete size of the promotion
    'base_price': [],
    'discount_perc': [],
    'discount_amt': [],
    'account_id': ['C'],  # account
    'product_brandkey': ['C'],  # brand
    'product_6_bc': ['C'],  # segment
    'product_3_cat': ['C'],  # category
    'week_nr': ['C'],
    'mechanism': ['C'],
    'multi_buy_x': [],
    'multi_buy_y': [],
    # 'field_102401': [],
    'promotion_dimension_136': ['C'],
    'promotion_dimension_137': ['C'],
    # 'promotion_dimension_138': ['C']
}

# we predict the lift normally or log?
prediction_model.target = {'lift': ['log']}

# are we doing logarithmic prediction?
if 'log' in prediction_model.target['lift']:
    log = True
else:
    log = False

# Create train and test sets

In [9]:
# get only use the needed columns
used_column_list = list(set(prediction_model.features.keys() + prediction_model.target.keys()))

# create a mask based on random selections or on a period
mask = np.random.rand(len(df)) < 0.8

# create train sets
train_df, train_lift, test_df, test_lift = create_train_test_sets(df[used_column_list], mask, prediction_model, prediction_target='lift')

# are we doing logarithmic predictions
if log:
    # we need to train everything based on the log value
    train_lift = train_lift.apply(np.log)


Train set: 55576
Test set: 14124


# Select a regressor

In [10]:
# create and train a regressor
regressor = ensemble.ExtraTreesRegressor(n_estimators=79,
                                         random_state=10,
                                         min_samples_split=4,
                                         n_jobs=-1)
regressor.fit(train_df, train_lift)

ExtraTreesRegressor(bootstrap=False, criterion='mse', max_depth=None,
          max_features='auto', max_leaf_nodes=None,
          min_impurity_split=1e-07, min_samples_leaf=1,
          min_samples_split=4, min_weight_fraction_leaf=0.0,
          n_estimators=79, n_jobs=-1, oob_score=False, random_state=10,
          verbose=0, warm_start=False)

# Predict and score the model

In [11]:
# predict the lift
predict_lift = regressor.predict(test_df)

if log:
    # if it was logarithmic, expand the lift again
    predict_lift = np.exp(predict_lift)

# score the model
score_model(predict_lift, test_lift, baseline=test_df['baseline_units'])

R²:0.581930268159
MAE:1.58510930616
MAPE:25.6168025772
Forecast error:21.9045260691


# Check Feature Importance

In [12]:
# Retrieve the feature importance
feature_importance = regressor.feature_importances_
feature_importance = 100.0 * (feature_importance / feature_importance.max())
mask = feature_importance > 0.5
feature_importance = feature_importance[mask]
sorted_idx = np.argsort(feature_importance)
output_list = []
for val, feature in zip(feature_importance[sorted_idx], train_df.columns[sorted_idx]):
    output_list.append({'feature': feature, 'importance': val})
importance_df = pd.DataFrame(output_list)
importance_df = importance_df.sort('importance', ascending=False)

# now plot a chart
label = cat(columns='feature', sort=False)
p = Bar(importance_df, label=label, values='importance', legend=None)
p.axis[1].axis_label = 'Importance'
show(p)

# Investigate Results

In [45]:
label_lookup = {v: k for k,v in prediction_model.labels.iteritems()}

# check where we are off
test_df['count'] = 1
test_df['lift_act'] = test_lift
test_df['lift_pred'] = predict_lift
test_df['total_units_act'] = test_df['baseline_units'] * test_df['lift_act']
test_df['total_units_pred'] = test_df['baseline_units'] * test_df['lift_pred']

In [16]:
# result: prediction vs actual -> plot + line etc. <- we will copy stuff from the investigation part
# plot scatter diagrams for correlation visualization
check_list = [('total_units_act', 'total_units_pred')]

# now plot
for col_x, col_y in check_list:
    if test_df[col_x].dtype in [np.int64, np.float64] and test_df[col_y].dtype in [np.int64, np.float64]:
        print('Drawing Scatter Correlation for ' + col_x + ' and ' + col_y)
        p = Scatter(test_df, x=col_x, y=col_y)
        show(p)
    else:
        print('Both columns need to be numerical')

Drawing Scatter Correlation for total_units_act and total_units_pred


In [46]:
# charts that check against variance
check_list = ['discount_perc', 'account_id', 'mechanism']

# now plot
for col in check_list:
    if df[col].dtype in [np.int64, np.float64]:
        print('Drawing Average Difference + Nr Observations for ' + col)
        test_df['tmp_col'] = test_df[col].round() 
        group = test_df.groupby(['tmp_col'], as_index=False)['total_units_act', 'total_units_pred', 'count'].sum()
        del test_df['tmp_col']
        group['variance'] = group['total_units_pred'] / group['total_units_act'] * 100.0
        group = group.rename(columns={'tmp_col': col})
        p = Line(group, x=col, y='variance')
        show(p)
        p = Line(group, x=col, y='count', color='green')
        show(p) 
    else:
        print('Showing ' + col + ' Average Lift for ' + str(top_def) + ' most used')
        group = test_df.groupby([col], as_index=False)['total_units_act', 'total_units_pred', 'count'].sum()
        group[col] = group[col].apply(lambda x: label_lookup.get(x, 'Unknown').encode('utf-8'))
        group = group.nlargest(top_def, 'count')
        group['variance'] = group['total_units_pred'] / group['total_units_act'] * 100.0
        label = cat(columns=col, sort=False)
        p = Bar(group, label=label, values='variance', legend=None)
        p.axis[1].axis_label = 'Total Variance'
        show(p) 

Drawing Average Difference + Nr Observations for discount_perc


Showing account_id Average Lift for 20 most used


Showing mechanism Average Lift for 20 most used


# Save the Model

In [12]:
# save the model
prediction_model.model = regressor
prediction_model.save()